In [1]:
import os
import sys

from src.denoising_diffusion_pytorch import GaussianDiffusion
from src.residual_denoising_diffusion_pytorch import (
    ResidualDiffusion,
    Trainer,
    Unet,
    UnetRes,
    set_seed,
)

# init
os.environ["CUDA_VISIBLE_DEVICES"] = ",".join(str(e) for e in [0])
sys.stdout.flush()
set_seed(10)
debug = False
if debug:
    save_and_sample_every = 2
    sampling_timesteps = 10
    sampling_timesteps_original_ddim_ddpm = 10
    train_num_steps = 200
else:
    save_and_sample_every = 1000
    sampling_timesteps = 5
    sampling_timesteps_original_ddim_ddpm = 250
    train_num_steps = 30000

original_ddim_ddpm = False
if original_ddim_ddpm:
    condition = False
    input_condition = False
    input_condition_mask = False
else:
    condition = True
    input_condition = True
    input_condition_mask = True

if condition:
    if input_condition:
        folder = [
            "/home/shenss/python/arcface-pytorch/datasets/talfw",
            "/home/shenss/python/arcface-pytorch/datasets/talfw",
            "/home/shenss/python/arcface-pytorch/datasets/talfw",
            "/home/shenss/python/arcface-pytorch/datasets/talfw",
            "/home/shenss/python/arcface-pytorch/datasets/talfw",
            "/home/shenss/python/arcface-pytorch/datasets/talfw",
        ]
    else:
        folder = [
            "/home/shenss/python/dataset/Celebrity Face Image Dataset/train/gt",
            "/home/shenss/python/dataset/Celebrity Face Image Dataset/train/input_ht_rgb",
            "/home/shenss/python/dataset/Celebrity Face Image Dataset/test/gt",
            "/home/shenss/python/dataset/Celebrity Face Image Dataset/test/input_ht_rgb",
        ]
    train_batch_size = 1
    num_samples = 1
    sum_scale = 1
    image_size = 112
else:
    folder = "/home/shenss/python/dataset/CelebA/img_align_celeba"
    train_batch_size = 32
    num_samples = 25
    sum_scale = 1
    image_size = 32

if original_ddim_ddpm:
    model = Unet(dim=64, dim_mults=(1, 2, 4, 8))
    diffusion = GaussianDiffusion(
        model,
        image_size=image_size,
        timesteps=1000,  # number of steps
        sampling_timesteps=sampling_timesteps_original_ddim_ddpm,
        loss_type="l1",  # L1 or L2
    )
else:
    model = UnetRes(
        dim=64,
        dim_mults=(1, 2, 4, 8),
        share_encoder=0,  # 1 0 -1，分别对应共享编码器、两个独立的 U-Net 和一个独立的 U-Net。
        condition=condition,
        input_condition=input_condition,
    )
    diffusion = ResidualDiffusion(
        model,
        image_size=image_size,
        timesteps=1000,  # number of steps
        # number of sampling timesteps (using ddim for faster inference [see citation for ddim paper])
        sampling_timesteps=sampling_timesteps,
        objective="pred_res_noise",  # pred_res_noise, pred_res, pred_noise
        loss_type="l1",  # L1 or L2 or huber(SmoothL1)
        condition=condition,
        sum_scale=sum_scale,
        input_condition=input_condition,
        input_condition_mask=input_condition_mask,
    )

trainer = Trainer(
    diffusion,
    folder,
    train_batch_size=train_batch_size,
    num_samples=num_samples,
    train_lr=8e-5,
    train_num_steps=train_num_steps,  # total training steps
    gradient_accumulate_every=2,  # gradient accumulation steps
    ema_decay=0.995,  # exponential moving average decay
    amp=False,  # turn on mixed precision
    convert_image_to="RGB",
    condition=condition,
    save_and_sample_every=save_and_sample_every,
    equalizeHist=False,
    crop_patch=False,
    generation=False,
    halftone="fs",
    gaussian_filter=True,
    get_sobel="wsobel",
)

In [2]:
# test
if not trainer.accelerator.is_local_main_process:
    pass
else:
    #Train_DiffSo_FS_Gaussian_ts5_30K
    #trainer.load(trainer.train_num_steps//save_and_sample_every)
    epoch = 30
    trainer.load(epoch)
    trainer.set_results_folder(f'./results/DiffSo_FS_Gaussian_ts{sampling_timesteps}_ep{epoch}_TALFW')
    trainer.test(last=True, save_parent=True)

/home/shenss/python/DiffSo/src/residual_denoising_diffusion_pytorch.py:1572: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  data = torch.load(str(path), map_location=self.dev

load model - results/sample/model-30.pt
test start


sampling loop time step:   0%|          | 0/5 [00:00<?, ?it/s]

test-save Yoshiyuki_Kamei_0001.jpg


sampling loop time step:   0%|          | 0/5 [00:00<?, ?it/s]

...

test-save Mike_Tyson_0001.jpg


sampling loop time step:   0%|          | 0/5 [00:00<?, ?it/s]

test-save Mike_Tyson_0003.jpg


sampling loop time step:   0%|          | 0/5 [00:00<?, ?it/s]

test-save Craig_MacTavish_0001.jpg
test end


In [4]:


import os
import shutil
from pathlib import Path

InvPath = '/home/shenss/python/DiffSo/results/DiffSo_FS_Gaussian_ts5_ep10_TALFW'
output_base_path = '/home/shenss/python/arcface-pytorch/datasets/TALFW_InvHT'  # 替换为你的输出目录路径

# 确保输出目录存在
os.makedirs(output_base_path, exist_ok=True)

for img in os.listdir(InvPath):
    if img.endswith(('.jpg', '.jpeg', '.png', '.tiff')):
        # 获取图片的基名（不带扩展名）
        img_basename = os.path.splitext(img)[0]
        
        # 提取文件夹名称（形如 firstname_lastname）
        folder_name = '_'.join(img_basename.split('_')[:-1])
        
        # 创建以图片基名命名的文件夹
        output_dir = Path(output_base_path) / folder_name
        os.makedirs(output_dir, exist_ok=True)
        
        # 构建源文件路径和目标文件路径
        src_path = Path(InvPath) / img
        dst_path = output_dir / img
        
        # 复制图片到目标文件夹
        shutil.copy(src_path, dst_path)
        print(f'Copied {src_path} to {dst_path}')

Copied /home/shenss/python/DiffSo/results/DiffSo_FS_Gaussian_ts5_ep10_TALFW/Hal_Gehman_0004.jpg to /home/shenss/python/arcface-pytorch/datasets/TALFW_InvHT/Hal_Gehman/Hal_Gehman_0004.jpg
Copied /home/shenss/python/DiffSo/results/DiffSo_FS_Gaussian_ts5_ep10_TALFW/Kim_Weeks_0001.jpg to /home/shenss/python/arcface-pytorch/datasets/TALFW_InvHT/Kim_Weeks/Kim_Weeks_0001.jpg
Copied /home/shenss/python/DiffSo/results/DiffSo_FS_Gaussian_ts5_ep10_TALFW/Larry_Johnson_0001.jpg to /home/shenss/python/arcface-pytorch/datasets/TALFW_InvHT/Larry_Johnson/Larry_Johnson_0001.jpg
Copied /home/shenss/python/DiffSo/results/DiffSo_FS_Gaussian_ts5_ep10_TALFW/Colleen_Atwood_0001.jpg to /home/shenss/python/arcface-pytorch/datasets/TALFW_InvHT/Colleen_Atwood/Colleen_Atwood_0001.jpg
Copied /home/shenss/python/DiffSo/results/DiffSo_FS_Gaussian_ts5_ep10_TALFW/Dennis_Kucinich_0007.jpg to /home/shenss/python/arcface-pytorch/datasets/TALFW_InvHT/Dennis_Kucinich/Dennis_Kucinich_0007.jpg
Copied /home/shenss/python/DiffS